In [2]:
from workerDECONVOLUTION_BBD103smTAD import *
from ioMicro import *

### Experiment 101 is on Kiwi

In [3]:
intron_flds = glob.glob(r'\\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H*I*')
exon_flds = glob.glob(r'\\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H*Q*')

In [ ]:
'\\\\merfish7\\merfish7v2\\20230515D101Myh67d15\\RNA\\H11_Q31_32_33'

In [4]:
exon_flds[1]

'\\\\merfish7\\merfish7v2\\20230515D101Myh67d15\\RNA\\H11_Q31_32_33'

### Check some fields of view to determine waht you can use as a PSF reference

In [5]:
fld = exon_flds[1]
fovs = glob.glob(fld+os.sep+'*.zarr')
print(fld)

\\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H11_Q31_32_33


In [17]:
im = read_im(fovs[90])#[50,53,54,30,0,90]
import napari
napari.view_image(im[1])##color

Viewer(axes=Axes(visible=False, labels=True, colored=True, dashed=False, arrows=True), camera=Camera(center=(0.0, 1023.5, 1023.5), zoom=0.3279541015625, angles=(0.0, 0.0, 90.0), perspective=0.0, interactive=True), cursor=Cursor(position=(25.0, 1.0, 0.0), scaled=True, size=1, style=<CursorStyle.STANDARD: 'standard'>), dims=Dims(ndim=3, ndisplay=2, last_used=0, range=((0.0, 50.0, 1.0), (0.0, 2048.0, 1.0), (0.0, 2048.0, 1.0)), current_step=(25, 1024, 1024), order=(0, 1, 2), axis_labels=('0', '1', '2')), grid=GridCanvas(stride=1, shape=(-1, -1), enabled=False), layers=[<Image layer 'Image' at 0x1cca07a4940>], scale_bar=ScaleBar(visible=False, colored=False, color=array([1., 0., 1., 1.], dtype=float32), ticks=True, position=<Position.BOTTOM_RIGHT: 'bottom_right'>, font_size=10.0, box=False, box_color=array([0. , 0. , 0. , 0.6], dtype=float32), unit=None), text_overlay=TextOverlay(visible=False, color=array([0.5, 0.5, 0.5, 1. ], dtype=float32), font_size=10.0, position=<TextOverlayPosition.T

### 1. Compute PSF

In [6]:
psfs = []

In [7]:
for ifov in tqdm([50,53,54,30,0,90]):
    im = read_im(fovs[ifov])[1]  ######Needs to match what you explored
    im_ = np.array(im[1:],dtype=np.float32)
    psf = get_psf(im_,th=1000,th_cor = 0.75,delta=3,delta_fit = 7,sxyzP = [15,60,60])
    psfs.append(psf)
#napari.view_image(im)
psff = np.mean([psf for psf in psfs if psf is not None],axis=0)
psff_ = np.array([p-np.median(p) for p in psff])
from scipy.ndimage import median_filter
psff_med = median_filter(psff_, size=15)
psfff = (psff_-psff_med)[5:-5,5:-5,5:-5][:-1,:-1,:-1]
psfff[psfff<0]=0
psfff = psfff/np.max(psfff)
#np.save(r'D:\Carlos\Scripts\psfs\psf_647_Kiwi.npy',psfff)

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [02:42<00:00, 27.05s/it]


In [33]:
import napari
napari.view_image(psfff)

Viewer(axes=Axes(visible=False, labels=True, colored=True, dashed=False, arrows=True), camera=Camera(center=(0.0, 54.5, 54.5), zoom=4.810454545454545, angles=(0.0, 0.0, 90.0), perspective=0.0, interactive=True), cursor=Cursor(position=(10.0, 1.0, 0.0), scaled=True, size=1, style=<CursorStyle.STANDARD: 'standard'>), dims=Dims(ndim=3, ndisplay=2, last_used=0, range=((0.0, 20.0, 1.0), (0.0, 110.0, 1.0), (0.0, 110.0, 1.0)), current_step=(10, 55, 55), order=(0, 1, 2), axis_labels=('0', '1', '2')), grid=GridCanvas(stride=1, shape=(-1, -1), enabled=False), layers=[<Image layer 'psfff' at 0x2746cac7b20>], scale_bar=ScaleBar(visible=False, colored=False, color=array([1., 0., 1., 1.], dtype=float32), ticks=True, position=<Position.BOTTOM_RIGHT: 'bottom_right'>, font_size=10.0, box=False, box_color=array([0. , 0. , 0. , 0.6], dtype=float32), unit=None), text_overlay=TextOverlay(visible=False, color=array([0.5, 0.5, 0.5, 1. ], dtype=float32), font_size=10.0, position=<TextOverlayPosition.TOP_LEFT:

In [10]:
#im_raw = np.array(im[1],dtype=np.float32)
im_raw = np.array(im,dtype=np.float32)

In [11]:
im_dec = full_deconv(im_raw,s_=500,pad=100,psf=psfff,parameters={'method': 'wiener', 'beta': 0.001, 'niter': 50},gpu=True,force=False)

100%|██████████████████████████████████████████████████████████████████████████████████| 25/25 [00:05<00:00,  4.48it/s]


In [42]:
v = napari.view_image(im_raw)
v.add_image(im_dec,contrast_limits=[0,np.percentile(im_dec,99.99)])

<Image layer 'im_dec' at 0x275fa1275e0>

### 2. Compute flat field correction

In [47]:
data_fld = r'\\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H11_Q31_32_33'
save_folder = r'D:\Carlos\Scripts\flat_field'
if not os.path.exists(save_folder): os.makedirs(save_folder)

In [48]:
compute_flat_field_raw(data_fld=data_fld,
    save_folder=save_folder,tag='Kiwi',
    ncols=4)### 750,cy5,cy3,405

100%|████████████████████████████████████████████████████████████████████████████████| 399/399 [02:33<00:00,  2.60it/s]


In [1]:
from workerDECONVOLUTION_BBD101comp import *
from ioMicro import *

In [2]:
main_f(['',0],try_mode=False)

Computing fitting on: Conv_zscan__000.zarr
131 ['\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H10_R10', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H11_R11', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H12_R12', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H13_R13', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H14_R14', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H15_R15', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H16_R16', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H17_R17', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H18_R18', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H19_R19', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H1_R1', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H20_R20', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H2

100%|███████████████████████████████████████████████████████████████████████████████| 131/131 [00:00<00:00, 247.11it/s]


Computing drift on: Conv_zscan__000.zarr


  0%|                                                                                          | 0/131 [00:00<?, ?it/s]

Loading: \\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H10_Q28_29_30\Conv_zscan__000.zarr
Finding markers...


...


100%|████████████████████████████████████████████████████████████████████████████████████| 7/7 [00:00<00:00,  8.67it/s]

100%|████████████████████████████████████████████████████████████████████████████████████| 7/7 [00:01<00:00,  5.11it/s]


Finding rough drift...


100%|██████████████████████████████████████████████████████████████████████████████| 131/131 [1:11:47<00:00, 32.88s/it]

Finding fine drift...


['', 0]

In [ ]:
#started running d101 whole dataset, @ 1:30 pm on 8/2/2023
errors = []
for i in range(0,399):
    try:
        main_f(['',i],try_mode=True)
    
    except:
        print("there is an error at: "+ str(i)) 
        errors.append(i)
    

Computing fitting on: Conv_zscan__000.zarr
132 ['\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H10_R10', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H11_R11', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H12_R12', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H13_R13', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H14_R14', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H15_R15', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H16_R16', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H17_R17', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H18_R18', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H19_R19', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H1_R1', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H20_R20', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H2

100%|███████████████████████████████████████████████████████████████████████████████| 132/132 [00:00<00:00, 248.86it/s]


Computing drift on: Conv_zscan__000.zarr
Computing fitting on: Conv_zscan__001.zarr
132 ['\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H10_R10', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H11_R11', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H12_R12', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H13_R13', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H14_R14', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H15_R15', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H16_R16', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H17_R17', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H18_R18', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H19_R19', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H1_R1', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H20_R20', '\\\\merfish8\\merfish8v2

100%|███████████████████████████████████████████████████████████████████████████████| 132/132 [00:00<00:00, 173.36it/s]


Computing drift on: Conv_zscan__001.zarr
Computing fitting on: Conv_zscan__002.zarr
132 ['\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H10_R10', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H11_R11', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H12_R12', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H13_R13', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H14_R14', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H15_R15', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H16_R16', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H17_R17', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H18_R18', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H19_R19', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H1_R1', '\\\\merfish8\\merfish8v2\\20230515D101Myh67d15\\DNA_singleCy5\\H20_R20', '\\\\merfish8\\merfish8v2

...

Finding fine drift...
Loading: \\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H7_I19_20_21\Conv_zscan__055.zarr
Finding markers...



100%|████████████████████████████████████████████████████████████████████████████████████| 7/7 [00:01<00:00,  5.31it/s]

100%|████████████████████████████████████████████████████████████████████████████████████| 7/7 [00:02<00:00,  2.77it/s]


Finding rough drift...


 48%|███████████████████████████████████████▎                                         | 64/132 [32:19<31:42, 27.98s/it]

Finding fine drift...
Loading: \\merfish7\merfish7v2\20230515D101Myh67d15\RNA\H8_I22_23_24\Conv_zscan__055.zarr


In [ ]:
# started running @ 9:10 pm on 8/2/23
# computation of all of D101
# restarted recomputation, including small tad cyngle cy5 8/3/23 @ 10:44 pm

In [ ]:
Open a new Anaconda propt and run:
>activate cellpose&&python D:\Carlos\Scripts\workerDECONVOLUTION_BBD101comp.py